In [1]:
!git clone https://github.com/ultralytics/yolov5  # clone
%cd yolov5
%pip install -qr requirements.txt  # install

import torch
import utils
display = utils.notebook_init()  # checks

YOLOv5 🚀 v7.0-210-gdd10481 Python-3.10.12 torch-2.0.1+cu118 CUDA:0 (NVIDIA A100-SXM4-40GB, 40514MiB)


Setup complete ✅ (12 CPUs, 83.5 GB RAM, 26.3/166.8 GB disk)


In [2]:
!pip install dropbox
!pip install twilio
!pip install mediapipe

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 594.0/594.0 kB 10.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 162.3/162.3 kB 21.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.6/49.6 kB 7.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.8/1.8 MB 22.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 33.5/33.5 MB 57.1 MB/s eta 0:00:00


In [3]:
import cv2
import mediapipe as mp
import os
import numpy as np
import torch
from google.colab.patches import cv2_imshow
import zipfile
import shutil
import glob
import pandas as pd
import numpy as np
import dropbox
import seaborn as sn

from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MinMaxScaler
from tensorflow.keras.models import Sequential
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import StandardScaler
from imblearn.over_sampling import SMOTE
from tensorflow.keras.layers import LSTM, Dense,BatchNormalization
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import GridSearchCV
from sklearn.metrics import classification_report
from sklearn.metrics import confusion_matrix
from sklearn.metrics import accuracy_score
from sklearn.model_selection import GridSearchCV

import numpy as np
import pandas as pd
import tensorflow as tf

import lightgbm as lgb
import xgboost as xgb

import matplotlib.pyplot as plt
import gc

from twilio.rest import Client

In [4]:

# Dropbox access token
access_token = "sl.BkG3jV1E6yFfCEqN_mYDcykwYvuv9lJT-h-6vz3fgLWVZv9RBTMAFeSotWJ2a5lFu9pl4fBuwRgCQ0AE3vZFE-d5QkANpdGwSQJOfLUhHbJGaZJ3KCo901Fzl0uzQqkpUlmoM0PbrOOUSQbF4MJHaio"

# Create a Dropbox instance
dbx = dropbox.Dropbox(access_token)
dbx

In [5]:
dropbox_folder_path="/Anomaly-Detection-Dataset"
files = dbx.files_list_folder(dropbox_folder_path)


In [6]:
try:
    response = dbx.files_list_folder(dropbox_folder_path)
    for entry in response.entries:
        # Check if the entry represents a file
        if isinstance(entry, dropbox.files.FileMetadata):
            # Extract the file name from the entry
            file_name = entry.name
            print(f"File: {file_name}")
        elif isinstance(entry, dropbox.files.FolderMetadata):
            # This is a folder entry, you can handle it here if needed
            folder_name = entry.name
            print(f"Folder: {folder_name}")
except dropbox.exceptions.AuthError as e:
    print("Error: Invalid Dropbox access token.")
except dropbox.exceptions.ApiError as e:
    print(f"Error: {e.user_message_text}")

File: Anomaly-Videos-Part-1.zip
File: Anomaly-Videos-Part-2.zip
File: Anomaly-Videos-Part-3.zip
File: Anomaly-Videos-Part-4.zip
File: Anomaly_Train.txt
File: Normal_Videos_for_Event_Recognition.zip
File: ReadMe-Anomaly-Detection.txt
File: Temporal_Anomaly_Annotation_for_Testing_Videos.txt
File: Testing_Normal_Videos.zip
File: Training-Normal-Videos-Part-1.zip
File: Training-Normal-Videos-Part-2.zip
File: UCF_Crimes-Train-Test-Split.zip


In [7]:
DESTINATION_DIRECTORY="/content"
DROPBOX_ZIP_FILE_PATH="/Anomaly-Detection-Dataset/"

def zip_upload(DROPBOX_ZIP_FILE_PATH,DESTINATION_DIRECTORY):
  try:
      _, response = dbx.files_download(DROPBOX_ZIP_FILE_PATH)

      # Save the zip file locally
      with open("temp.zip", "wb") as f:
          f.write(response.content)

      # Extract the contents of the zip file
      with zipfile.ZipFile("temp.zip", "r") as zip_ref:
          zip_ref.extractall(DESTINATION_DIRECTORY)

      print("Zip file extracted successfully.")
  except dropbox.exceptions.AuthError as e:
      print("Error: Invalid Dropbox access token.")
  except dropbox.exceptions.ApiError as e:
      print(f"Error: {e.user_message_text}")

  # Remove the temporary zip file
  import os
  os.remove("temp.zip")

zip_lst=['Anomaly-Videos-Part-1.zip','Anomaly-Videos-Part-2.zip','Anomaly-Videos-Part-3.zip','Anomaly-Videos-Part-4.zip','Normal_Videos_for_Event_Recognition.zip']

for i in zip_lst:
  print(DROPBOX_ZIP_FILE_PATH+i)
  zip_upload(DROPBOX_ZIP_FILE_PATH+i,DESTINATION_DIRECTORY)

/Anomaly-Detection-Dataset/Anomaly-Videos-Part-1.zip
Zip file extracted successfully.
/Anomaly-Detection-Dataset/Anomaly-Videos-Part-2.zip
Zip file extracted successfully.
/Anomaly-Detection-Dataset/Anomaly-Videos-Part-3.zip
Zip file extracted successfully.
/Anomaly-Detection-Dataset/Anomaly-Videos-Part-4.zip
Zip file extracted successfully.
/Anomaly-Detection-Dataset/Normal_Videos_for_Event_Recognition.zip
Zip file extracted successfully.


In [8]:

# Specify the source and destination paths for the files you want to move
move_lst=['Anomaly-Videos-Part-1/','Anomaly-Videos-Part-2/','Anomaly-Videos-Part-3/','Anomaly-Videos-Part-4/','Normal_Videos_for_Event_Recognition/']

# Specify the source and destination folder paths
SOURCE_FOLDER_PATH = "/content/"
DESTINATION_FOLDER_PATH = "/content/Anomaly_Videos/"

# Create the destination folder if it doesn't exist
if not os.path.exists(DESTINATION_FOLDER_PATH):
    os.makedirs(DESTINATION_FOLDER_PATH)

# Move all contents of the source folder to the destination folder
for i in move_lst:
  print(SOURCE_FOLDER_PATH+i)
  SOURCE_FOLDER_PATH_=SOURCE_FOLDER_PATH+i
  for item in os.listdir(SOURCE_FOLDER_PATH_):
      source_item_path = os.path.join(SOURCE_FOLDER_PATH_, item)
      destination_item_path = os.path.join(DESTINATION_FOLDER_PATH, item)

      # Use shutil.move to move the item to the destination folder
      shutil.move(source_item_path, destination_item_path)


/content/Anomaly-Videos-Part-1/
/content/Anomaly-Videos-Part-2/
/content/Anomaly-Videos-Part-3/
/content/Anomaly-Videos-Part-4/
/content/Normal_Videos_for_Event_Recognition/


In [9]:
normal_lst= glob.glob("/content/Anomaly_Videos/Normal*")
normal_lst

['/content/Anomaly_Videos/Normal_Videos_439_x264.mp4',
 '/content/Anomaly_Videos/Normal_Videos_641_x264.mp4',
 '/content/Anomaly_Videos/Normal_Videos_881_x264.mp4',
 '/content/Anomaly_Videos/Normal_Videos_912_x264.mp4',
 '/content/Anomaly_Videos/Normal_Videos_597_x264.mp4',
 '/content/Anomaly_Videos/Normal_Videos_310_x264.mp4',
 '/content/Anomaly_Videos/Normal_Videos_150_x264.mp4',
 '/content/Anomaly_Videos/Normal_Videos_656_x264.mp4',
 '/content/Anomaly_Videos/Normal_Videos_758_x264.mp4',
 '/content/Anomaly_Videos/Normal_Videos_345_x264.mp4',
 '/content/Anomaly_Videos/Normal_Videos_417_x264.mp4',
 '/content/Anomaly_Videos/Normal_Videos_704_x264.mp4',
 '/content/Anomaly_Videos/Normal_Videos_360_x264.mp4',
 '/content/Anomaly_Videos/Normal_Videos_247_x264.mp4',
 '/content/Anomaly_Videos/Normal_Videos_129_x264.mp4',
 '/content/Anomaly_Videos/Normal_Videos_696_x264.mp4',
 '/content/Anomaly_Videos/Normal_Videos_798_x264.mp4',
 '/content/Anomaly_Videos/Normal_Videos_634_x264.mp4',
 '/content

In [10]:
DESTINATION_FOLDER_PATH='/content/Anomaly_Videos/Normal'
if not os.path.exists(DESTINATION_FOLDER_PATH):
    os.makedirs(DESTINATION_FOLDER_PATH)
for i in normal_lst:
  shutil.move(i, DESTINATION_FOLDER_PATH)

class_vid_lst=glob.glob("/content/Anomaly_Videos/*")
class_vid_lst=[ x for x in class_vid_lst if "yolo" not in x and "zip" not in x ]

In [11]:
for class_vid in class_vid_lst:
  video_paths=glob.glob(class_vid+"/*")
  video_paths=video_paths[5:10]
  print(video_paths)

['/content/Anomaly_Videos/Assault/Assault016_x264.mp4', '/content/Anomaly_Videos/Assault/Assault024_x264.mp4', '/content/Anomaly_Videos/Assault/Assault018_x264.mp4', '/content/Anomaly_Videos/Assault/Assault036_x264.mp4', '/content/Anomaly_Videos/Assault/Assault038_x264.mp4']
['/content/Anomaly_Videos/Robbery/Robbery107_x264.mp4', '/content/Anomaly_Videos/Robbery/Robbery104_x264.mp4', '/content/Anomaly_Videos/Robbery/Robbery016_x264.mp4', '/content/Anomaly_Videos/Robbery/Robbery137_x264.mp4', '/content/Anomaly_Videos/Robbery/Robbery055_x264.mp4']
['/content/Anomaly_Videos/Stealing/Stealing082_x264.mp4', '/content/Anomaly_Videos/Stealing/Stealing059_x264.mp4', '/content/Anomaly_Videos/Stealing/Stealing014_x264.mp4', '/content/Anomaly_Videos/Stealing/Stealing015_x264.mp4', '/content/Anomaly_Videos/Stealing/Stealing010_x264.mp4']
['/content/Anomaly_Videos/Burglary/Burglary028_x264.mp4', '/content/Anomaly_Videos/Burglary/Burglary042_x264.mp4', '/content/Anomaly_Videos/Burglary/Burglary057_x

In [12]:
mp_pose = mp.solutions.pose
mp_drawing = mp.solutions.drawing_utils

In [15]:
model = torch.hub.load('ultralytics/yolov5', 'yolov5s', force_reload=True)  # yolov5n - yolov5x6 or custom

Downloading: "https://github.com/ultralytics/yolov5/zipball/master" to /root/.cache/torch/hub/master.zip
YOLOv5 🚀 v7.0-210-gdd10481 Python-3.10.12 torch-2.0.1+cu118 CUDA:0 (NVIDIA A100-SXM4-40GB, 40514MiB)

100%|██████████| 14.1M/14.1M [00:00<00:00, 20.0MB/s]

Fusing layers... 
YOLOv5s summary: 213 layers, 7225885 parameters, 0 gradients
Adding AutoShape... 


In [16]:
import gc
if  os.path.exists("/content/yolov5/runs/detect/exp"):
  print("exists")
  shutil.rmtree("/content/yolov5/runs/detect/exp")

In [17]:
import gc
if  os.path.exists("/content/yolov5/runs/detect/exp"):
  print("exists")
  shutil.rmtree("/content/yolov5/runs/detect/exp")
  video_paths=video_paths[:5]


In [18]:
master_df=pd.DataFrame()
for class_vid in class_vid_lst:
  video_paths=glob.glob(class_vid+"/*")
  video_paths=video_paths[:5]
  print(video_paths)
  master_dict = {}
  step=30
  frame_count =0
  for video_path in video_paths:
      cap = cv2.VideoCapture(video_path)
      frame_rate = cap.get(cv2.CAP_PROP_FPS)

      # Get the duration (in seconds)
      frame_count = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))
      fps = int(frame_rate)
      duration = frame_count // fps
      print(duration,fps)
      with mp_pose.Pose() as pose:
          video_dict = {}
          while cap.isOpened():
              success, frame = cap.read()
              if not success:
                  break
              frame_count += 1
              if frame_count % step == 0:
                results = model(frame)
                print(results)
                results.crop()
                lst=glob.glob("/content/yolov5/runs/detect/exp/crops/person/*")
                # print(lst)
                count=0
                for i in lst:
                    count=count+1
                    i=cv2.imread(i)
                    frame_rgb = cv2.cvtColor(i, cv2.COLOR_BGR2RGB)
                    results = pose.process(frame_rgb)
                    if results.pose_landmarks:
                        landmarks = results.pose_landmarks.landmark
                        keypoints = np.array([(lm.x, lm.y) for lm in landmarks])
                        shoulder_distance = np.linalg.norm(keypoints[mp_pose.PoseLandmark.LEFT_SHOULDER.value] - keypoints[mp_pose.PoseLandmark.RIGHT_SHOULDER.value])
                        elbow_distance = np.linalg.norm(keypoints[mp_pose.PoseLandmark.LEFT_ELBOW.value] - keypoints[mp_pose.PoseLandmark.RIGHT_ELBOW.value])

                        shoulder_angle = np.arctan2(keypoints[mp_pose.PoseLandmark.LEFT_SHOULDER.value, 1] - keypoints[mp_pose.PoseLandmark.RIGHT_SHOULDER.value, 1],
                                                    keypoints[mp_pose.PoseLandmark.LEFT_SHOULDER.value, 0] - keypoints[mp_pose.PoseLandmark.RIGHT_SHOULDER.value, 0])

                        arm_to_height_ratio = elbow_distance / (keypoints[mp_pose.PoseLandmark.LEFT_HIP.value, 1] - keypoints[mp_pose.PoseLandmark.RIGHT_HIP.value, 1])

                        frame_number = int(cap.get(cv2.CAP_PROP_POS_FRAMES))
                        frame_features = {
                            "shoulder_distance": shoulder_distance,
                            "elbow_distance": elbow_distance,
                            "shoulder_angle": shoulder_angle,
                            "arm_to_height_ratio": arm_to_height_ratio,
                            "Person_number" : count,
                            "Video_path" :video_path
                        }
                        video_dict[frame_number] = frame_features
                        print(frame_features)
                        del results,frame_rgb,landmarks,keypoints,shoulder_distance,elbow_distance,shoulder_angle,arm_to_height_ratio,frame_number
                        # video_dict["Person "+str(count)]=frame_features
                        gc.collect()

                master_dict[video_path] = video_dict
                print("-")
                if os.path.exists("/content/yolov5/runs/detect/exp"):
                  shutil.rmtree("/content/yolov5/runs/detect/exp")
                gc.collect()
      cap.release()
  rows = []
  for video_path, frame_data in master_dict.items():
      for frame_number, frame_info in frame_data.items():
          row = {'Video_path': video_path, 'Frame_number': frame_number}
          row.update(frame_info)
          rows.append(row)
  feature_df=pd.DataFrame()
  # Create the DataFrame
  feature_df = pd.DataFrame(rows)
  master_df=master_df.append(feature_df)
  # Display the DataFrame
  # print(df)

['/content/Anomaly_Videos/Assault/Assault047_x264.mp4', '/content/Anomaly_Videos/Assault/Assault032_x264.mp4', '/content/Anomaly_Videos/Assault/Assault020_x264.mp4', '/content/Anomaly_Videos/Assault/Assault003_x264.mp4', '/content/Anomaly_Videos/Assault/Assault009_x264.mp4']
111 30


Saved 1 image to runs/detect/exp
Saved results to runs/detect/exp



image 1/1: 240x320 2 cars
Speed: 12.6ms pre-process, 118.5ms inference, 32.3ms NMS per image at shape (1, 3, 480, 640)
-


Saved 1 image to runs/detect/exp
Saved results to runs/detect/exp



image 1/1: 240x320 2 cars
Speed: 3.0ms pre-process, 6.7ms inference, 1.5ms NMS per image at shape (1, 3, 480, 640)
-


...

Saved 1 image to runs/detect/exp
Saved results to runs/detect/exp



image 1/1: 240x320 1 person, 1 chair
Speed: 2.4ms pre-process, 7.0ms inference, 1.4ms NMS per image at shape (1, 3, 480, 640)
{'shoulder_distance': 0.47112695267310517, 'elbow_distance': 0.43225515427533845, 'shoulder_angle': -0.117505638584647, 'arm_to_height_ratio': -13.577798750052754, 'Person_number': 1, 'Video_path': '/content/Anomaly_Videos/Fighting/Fighting049_x264.mp4'}
-


Saved 1 image to runs/detect/exp
Saved results to runs/detect/exp



image 1/1: 240x320 (no detections)
Speed: 2.0ms pre-process, 6.6ms inference, 0.5ms NMS per image at shape (1, 3, 480, 640)
-


<ipython-input-18-b3cb0609d60d>:78: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  master_df=master_df.append(feature_df)


In [19]:
master_df.head()

Video_path  Frame_number  \
0  /content/Anomaly_Videos/Assault/Assault020_x26...           216   
1  /content/Anomaly_Videos/Assault/Assault020_x26...           276   
2  /content/Anomaly_Videos/Assault/Assault020_x26...           366   
3  /content/Anomaly_Videos/Assault/Assault020_x26...           396   
4  /content/Anomaly_Videos/Assault/Assault020_x26...           426   

   shoulder_distance  elbow_distance  shoulder_angle  arm_to_height_ratio  \
0           1.072564        1.223355       -0.048011          1729.980550   
1           0.443199        0.322144       -3.117326             9.401982   
2           0.242595        0.316337        0.000729            49.871323   
3           0.172158        0.290710        0.151696            -6.841270   
4           0.304112        0.293166        3.108030            65.838663   

   Person_number  
0              1  
1              4  
2              2  
3              1  
4              3

<ipython-input-90-fac2e90a530a>:5: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_2=df_1.append(df_1)


In [92]:
master_df = master_df.loc[:, ~master_df.columns.str.contains('^Unnamed')]
master_df.head()

Video_path  Frame_number  \
0  /content/Anomaly_Videos/Assault/Assault013_x26...            51   
1  /content/Anomaly_Videos/Assault/Assault013_x26...            81   
2  /content/Anomaly_Videos/Assault/Assault013_x26...           111   
3  /content/Anomaly_Videos/Assault/Assault013_x26...           141   
4  /content/Anomaly_Videos/Assault/Assault013_x26...           201   

   shoulder_distance  elbow_distance  shoulder_angle  arm_to_height_ratio  \
0           0.825352        1.380282       -2.921909           -12.669692   
1           0.233416        0.159275        3.090152           -11.746744   
2           0.917443        1.149235       -3.083697           -30.507757   
3           0.108606        0.059077       -3.065977             1.073312   
4           0.321555        0.125002        3.041822             2.429184   

   Person_number  
0              5  
1              2  
2              2  
3              3  
4              3

In [93]:
label=[]
for i in range(master_df.shape[0]):
  # print(i)
  strx=master_df.iloc[i]["Video_path"]
  # print(strx)
  if "Abuse" in strx:
    label.append("Abuse")
  elif "Arrest" in strx:
    label.append("Arrest")
  elif "Arson" in strx:
    label.append("Arson")#
  elif "Assult" in strx:
    label.append("Assult")#
  elif "Burglary" in strx:
    label.append("Burglary")
  elif "Fighting" in strx:
    label.append("Fighting")
  elif "Normal" in strx:
    label.append("Normal")
  elif "Robbery" in strx:
    label.append("Robbery")
  elif "Shooting" in strx:
    label.append("Shooting")
  elif "Shoplifting" in strx:
    label.append("Shoplifting")
  elif "Stealing" in strx:
    label.append("Stealing")#
  elif "Vandalism" in strx:
    label.append("Vandalism")
  else:
    label.append("Unknown")
master_df["Activity_Recognition_Label"]=label

In [94]:
master_df=master_df[~master_df["Activity_Recognition_Label"].isin(["Unknown"])]


In [95]:
master_df=master_df.drop(['Video_path'], axis=1)
susp_label=[]
for i in range(master_df.shape[0]):
  # print(i)
  strx=master_df.iloc[i]["Activity_Recognition_Label"]
  if "Normal" in strx:
    susp_label.append("Normal")
  else:
    susp_label.append("Suspicious")
master_df["Activity_Label"]=susp_label

In [96]:
# master_df.to_csv("Blazepose_sample.csv")

In [97]:
master_df.head()

Frame_number  shoulder_distance  elbow_distance  shoulder_angle  \
240           136           0.019738        0.058205       -2.675520   
241           166           0.244076        0.222307       -2.869226   
242           196           0.259568        0.347421       -3.024840   
243           826           0.041568        0.080042       -2.548320   
244          1036           0.285964        0.503714       -1.767956   

     arm_to_height_ratio  Person_number Activity_Recognition_Label  \
240             2.696296              1                  Vandalism   
241            -4.649397              1                  Vandalism   
242           -19.161695              1                  Vandalism   
243            -5.685189              1                  Vandalism   
244            -3.042181              1                  Vandalism   

    Activity_Label  
240     Suspicious  
241     Suspicious  
242     Suspicious  
243     Suspicious  
244     Suspicious

# TO DETECT IF THE ACTIVITY IS SUSPICIOUS OR NOT

In [98]:
features=['shoulder_distance', 'elbow_distance', 'shoulder_angle',
       'arm_to_height_ratio', 'Person_number']
le = LabelEncoder()
master_df['Activity_Label'] = le.fit_transform(master_df['Activity_Label'])
X = master_df.drop('Activity_Label', axis=1)[features].values
Y = master_df['Activity_Label'].values

In [99]:
num_classes=len(master_df["Activity_Label"].unique())
num_classes

2

In [100]:
X_train, X_test, y_train, y_test = train_test_split(X, Y, test_size=0.2, random_state=42)
# Standardize features using z-score normalization
scaler = StandardScaler()
X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)
smote = SMOTE(sampling_strategy='auto', random_state=42)
X_train, y_train = smote.fit_resample(X_train, y_train)
print(X_train.shape, X_test.shape, y_train.shape, y_test.shape)

(9838, 5) (1280, 5) (9838,) (1280,)


In [101]:
param_grid = {
    'n_estimators': [50, 100, 200],
    'max_depth': [None, 10, 20],
    'min_samples_split': [2, 5, 10],
    'min_samples_leaf': [1, 2, 4]
}

# Create a Random Forest classifier
rf_classifier = RandomForestClassifier(random_state=42)

# Create a GridSearchCV object
grid_search = GridSearchCV(estimator=rf_classifier, param_grid=param_grid, scoring='accuracy', cv=3)

# Fit the GridSearchCV object to the data
grid_search.fit(X_train, y_train)

# Get the best parameters and best score
best_params = grid_search.best_params_
best_score = grid_search.best_score_

print("Best Parameters:", best_params)
print("Best Score:", best_score)

# Evaluate the best model on the test data
best_model = grid_search.best_estimator_
test_accuracy = best_model.score(X_test, y_test)
print("Test Accuracy:", test_accuracy)

Best Parameters: {'max_depth': None, 'min_samples_leaf': 1, 'min_samples_split': 5, 'n_estimators': 200}
Best Score: 0.9851597502708788
Test Accuracy: 0.9890625


In [102]:
# Predict using the best estimator
y_pred = best_model.predict(X_test)

# Calculate accuracy
accuracy = accuracy_score(y_test, y_pred)
print("Best Parameters:", best_params)
print(classification_report(y_test, y_pred))

Best Parameters: {'max_depth': None, 'min_samples_leaf': 1, 'min_samples_split': 5, 'n_estimators': 200}
              precision    recall  f1-score   support

           0       0.88      0.84      0.86        51
           1       0.99      1.00      0.99      1229

    accuracy                           0.99      1280
   macro avg       0.94      0.92      0.93      1280
weighted avg       0.99      0.99      0.99      1280



In [103]:
y_test_original = le.inverse_transform(y_test)
y_pred_original = le.inverse_transform(y_pred)
print(classification_report(y_test_original, y_pred_original))

              precision    recall  f1-score   support

      Normal       0.88      0.84      0.86        51
  Suspicious       0.99      1.00      0.99      1229

    accuracy                           0.99      1280
   macro avg       0.94      0.92      0.93      1280
weighted avg       0.99      0.99      0.99      1280



In [104]:
import pickle
filename='rgb_sample.pkl'
pickle.dump(best_model,open(filename,'wb'))

# TO RECOGNIZE THE ACTIVITY TYPE

In [75]:
features=['shoulder_distance', 'elbow_distance', 'shoulder_angle',
       'arm_to_height_ratio', 'Person_number']
le = LabelEncoder()
master_df['Activity_Recognition_Label'] = le.fit_transform(master_df['Activity_Recognition_Label'])
X = master_df.drop('Activity_Recognition_Label', axis=1)[features].values
Y = master_df['Activity_Recognition_Label'].values

In [76]:
num_classes=len(master_df["Activity_Recognition_Label"].unique())
num_classes

11

In [77]:
X_train, X_test, y_train, y_test = train_test_split(X, Y, test_size=0.2, random_state=42)
print(X_train.shape, X_test.shape, y_train.shape, y_test.shape)

(5116, 5) (1280, 5) (5116,) (1280,)


In [78]:
scaler = StandardScaler()
X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)

In [79]:
smote = SMOTE(sampling_strategy='auto', random_state=42)
X_train, y_train = smote.fit_resample(X_train, y_train)
print(X_train.shape, X_test.shape, y_train.shape, y_test.shape)

(17699, 5) (1280, 5) (17699,) (1280,)


In [80]:


# Define the parameter grid to search through
param_grid = {
    'n_estimators': [25,50, 100],
    'max_depth': [1,3, 5, 7,9],
    'learning_rate': [0.01, 0.1, 0.2]
}

# Create an XGBoost classifier
xgb_classifier = xgb.XGBClassifier()

# Initialize GridSearchCV
grid_search = GridSearchCV(estimator=xgb_classifier, param_grid=param_grid, scoring='accuracy', cv=3)

# Perform the grid search on the data
grid_search.fit(X_train, y_train)

# Get the best parameters and best estimator from the grid search
best_params = grid_search.best_params_
best_estimator = grid_search.best_estimator_

# Predict using the best estimator
y_pred = best_estimator.predict(X_test)

# Calculate accuracy
accuracy = accuracy_score(y_test, y_pred)
print("Best Parameters:", best_params)
print("Best Accuracy:", accuracy)

Best Parameters: {'learning_rate': 0.2, 'max_depth': 11, 'n_estimators': 150}
Best Accuracy: 0.8703125


In [81]:
print(classification_report(y_test, y_pred))

              precision    recall  f1-score   support

           0       0.81      0.88      0.84        66
           1       0.85      0.87      0.86       185
           2       0.45      1.00      0.62         5
           3       0.95      0.90      0.92       383
           4       0.82      0.91      0.87       281
           5       0.81      0.84      0.83        51
           6       0.95      0.78      0.86        91
           7       1.00      0.89      0.94        19
           8       0.84      0.79      0.82       124
           9       0.83      0.78      0.81        37
          10       0.84      0.84      0.84        38

    accuracy                           0.87      1280
   macro avg       0.83      0.86      0.84      1280
weighted avg       0.88      0.87      0.87      1280



In [87]:
import pickle
filename='xgb_sample.pkl'
pickle.dump(best_estimator,open(filename,'wb'))

# Real Time Simulation

In [82]:
video_path="/content/youtube.mp4"

In [83]:
if  os.path.exists("/content/yolov5/runs/detect"):
  print("exists")
  shutil.rmtree("/content/yolov5/runs/detect")

exists


In [111]:
import os
from twilio.rest import Client


# Find your Account SID and Auth Token at twilio.com/console
# and set the environment variables. See http://twil.io/secure
# account_sid = os.environ['AC546208f0726a003ba5b04021deec1c72']
# auth_token = os.environ['22418083a5133cd1b923aac801955f47']
def alarm():
  account_sid = 'AC546208f0726a003ba5b04021deec1c72'
  auth_token = '22418083a5133cd1b923aac801955f47'
  client = Client(account_sid, auth_token)

  message = client.messages \
                  .create(
                      body="Suspicious activity Detected",
                      from_='+15304567490',
                      to='+353894147223'
                  )

  print(message.sid)
alarm()


SMcd8ed4138cf6864ee57dd4138b55fd04


In [109]:
step=30
master_dict = {}

cap = cv2.VideoCapture(video_path)
frame_rate = cap.get(cv2.CAP_PROP_FPS)
# Get the duration (in seconds)
frame_count = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))
fps = int(frame_rate)
duration = frame_count // fps
print(duration,fps)

with mp_pose.Pose() as pose:
    video_dict = {}
    while cap.isOpened():
        success, frame = cap.read()
        if not success:
            break
        frame_count += 1
        if frame_count % step == 0:
          # print("frame_count",frame_count)
          results = model(frame)
          # print(results)
          results.crop()
          lst=glob.glob("/content/yolov5/runs/detect/exp/crops/person/*")
          # print(lst)
          count=0
          for i in lst:
              count=count+1
              i=cv2.imread(i)
              frame_rgb = cv2.cvtColor(i, cv2.COLOR_BGR2RGB)
              results = pose.process(frame_rgb)
              if results.pose_landmarks:
                  landmarks = results.pose_landmarks.landmark
                  # print(landmarks)
                  keypoints = np.array([(lm.x, lm.y) for lm in landmarks])
                  shoulder_distance = np.linalg.norm(keypoints[mp_pose.PoseLandmark.LEFT_SHOULDER.value] - keypoints[mp_pose.PoseLandmark.RIGHT_SHOULDER.value])
                  elbow_distance = np.linalg.norm(keypoints[mp_pose.PoseLandmark.LEFT_ELBOW.value] - keypoints[mp_pose.PoseLandmark.RIGHT_ELBOW.value])

                  shoulder_angle = np.arctan2(keypoints[mp_pose.PoseLandmark.LEFT_SHOULDER.value, 1] - keypoints[mp_pose.PoseLandmark.RIGHT_SHOULDER.value, 1],
                                              keypoints[mp_pose.PoseLandmark.LEFT_SHOULDER.value, 0] - keypoints[mp_pose.PoseLandmark.RIGHT_SHOULDER.value, 0])

                  arm_to_height_ratio = elbow_distance / (keypoints[mp_pose.PoseLandmark.LEFT_HIP.value, 1] - keypoints[mp_pose.PoseLandmark.RIGHT_HIP.value, 1])

                  frame_number = int(cap.get(cv2.CAP_PROP_POS_FRAMES))
                  frame_features = {
                      "shoulder_distance": shoulder_distance,
                      "elbow_distance": elbow_distance,
                      "shoulder_angle": shoulder_angle,
                      "arm_to_height_ratio": arm_to_height_ratio,
                      "Person_number" : count,
                      "Video_path" :video_path
                  }

                  selected_features = [frame_features['shoulder_distance'], frame_features['shoulder_distance'],frame_features['shoulder_angle'],frame_features['arm_to_height_ratio'],frame_features['Person_number']]
                  features = np.array([selected_features])
                  rgb_predictions = best_model.predict(features)
                  if rgb_predictions[0] == 1:
                            print("Suspicious")
                            predictions = best_estimator.predict(features)
                            alarm()
                  video_dict[frame_number] = frame_features
                  # print("frame_features",frame_features)
                  # del results,frame_rgb,landmarks,keypoints,shoulder_distance,elbow_distance,shoulder_angle,arm_to_height_ratio,frame_number
                  # video_dict["Person "+str(count)]=frame_feature1
                  # gc.collect()
          master_dict[video_path] = video_dict
          print("-")
          if os.path.exists("/content/yolov5/runs/detect/exp"):
            shutil.rmtree("/content/yolov5/runs/detect/exp")
          # gc.collect()

cap.release()


Saved 1 image to runs/detect/exp
Saved results to runs/detect/exp

Saved 1 image to runs/detect/exp
Saved results to runs/detect/exp

Saved 1 image to runs/detect/exp
Saved results to runs/detect/exp



31 30
-
-


Saved 1 image to runs/detect/exp
Saved results to runs/detect/exp

Saved 1 image to runs/detect/exp
Saved results to runs/detect/exp

Saved 1 image to runs/detect/exp
Saved results to runs/detect/exp

Saved 1 image to runs/detect/exp
Saved results to runs/detect/exp



-
-
-
-


Saved 1 image to runs/detect/exp
Saved results to runs/detect/exp

Saved 1 image to runs/detect/exp
Saved results to runs/detect/exp

Saved 1 image to runs/detect/exp
Saved results to runs/detect/exp



...

Suspicious
-
Suspicious
Suspicious
-
Suspicious
-


Saved 1 image to runs/detect/exp
Saved results to runs/detect/exp

Saved 1 image to runs/detect/exp
Saved results to runs/detect/exp

Saved 1 image to runs/detect/exp
Saved results to runs/detect/exp

Saved 1 image to runs/detect/exp
Saved results to runs/detect/exp



Suspicious
-
Suspicious
-
Suspicious
-


Saved 1 image to runs/detect/exp
Saved results to runs/detect/exp



Suspicious
Suspicious
-
-
